### Analysis of Meridian Results


In [1]:
from utils import clean_numeric_dataframe

In [2]:
import sys, os
IN_COLAB = ('google.colab' in sys.modules) or ('COLAB_RELEASE_TAG' in os.environ)

In [3]:
# Install meridian: from PyPI @ latest release (robust in Colab and local Jupyter)
import sys, subprocess
pkg = "google-meridian[colab,and-cuda]" if IN_COLAB else "google-meridian"
print(f"Installing: {pkg}")
try:
    subprocess.check_call([sys.executable, "-m", "pip", "install", "--upgrade", pkg])
except Exception as e:
    print(f"pip install failed for {pkg}: {e}")

Installing: google-meridian


In [4]:
import arviz as az
import IPython
from meridian import constants
from meridian.analysis import analyzer
from meridian.analysis import formatter
from meridian.analysis import optimizer
from meridian.analysis import summarizer
from meridian.analysis import visualizer
from meridian.data import data_frame_input_data_builder as data_builder
from meridian.data import test_utils
from meridian.model import model
from meridian.model import prior_distribution
from meridian.model import spec
import numpy as np
import pandas as pd
# check if GPU is available
from psutil import virtual_memory
import tensorflow as tf
import tensorflow_probability as tfp

if IN_COLAB:
    from google.colab import drive


ram_gb = virtual_memory().total / 1e9
print('Your runtime has {:.1f} gigabytes of available RAM\n'.format(ram_gb))
print(
    'Num GPUs Available: ',
    len(tf.config.experimental.list_physical_devices('GPU')),
)
print(
    'Num CPUs Available: ',
    len(tf.config.experimental.list_physical_devices('CPU')),
)





Your runtime has 16.9 gigabytes of available RAM

Num GPUs Available:  0
Num CPUs Available:  1


In [35]:
## load from local
file_path = "Results\\saved_mmm_additive_halfprice3.pkl"
mmm_add = model.load_mmm(file_path)

In [36]:
mmm_summarizer_add = summarizer.Summarizer(mmm_add)
analyzer_add = analyzer.Analyzer(mmm_add)
mediaEffects_add = visualizer.MediaEffects(mmm_add)
model_diagnostics_add = visualizer.ModelDiagnostics(mmm_add)
model_fit_add = visualizer.ModelFit(mmm_add)
media_summary_add = visualizer.MediaSummary(mmm_add)


c:\Users\User\repos\MMM\.venv\Lib\site-packages\meridian\analysis\analyzer.py:590: UserWarning: The `aggregate_geos` argument is ignored in the national model. It will be reset to `True`.
  warnings.warn(


In [37]:

model_diagnostics_add.plot_prior_and_posterior_distribution()

alt.FacetChart(...)

In [38]:
model_fit_add.plot_model_fit(
                         include_baseline=False,
                         include_ci=False)

alt.Chart(...)

In [39]:
df_media_results = media_summary_add.summary_table()


c:\Users\User\repos\MMM\.venv\Lib\site-packages\meridian\analysis\visualizer.py:1629: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  .aggregate(lambda g: f'{g[0]} ({g[1]}, {g[2]})')


In [40]:
model_diagnostics_add.predictive_accuracy_table()

c:\Users\User\repos\MMM\.venv\Lib\site-packages\meridian\analysis\analyzer.py:590: UserWarning: The `aggregate_geos` argument is ignored in the national model. It will be reset to `True`.
  warnings.warn(


metric geo_granularity     value
0  R_Squared        national  0.926092
1       MAPE        national  0.038002
2      wMAPE        national  0.036823

In [41]:
base_dir = 'Results'
df_rois = pd.read_csv(os.path.join(base_dir, 'rois_add.csv'))
df_decomp_vol = pd.read_csv(os.path.join(base_dir, 'decomp_add.csv'))
df_var_spec = pd.read_csv(os.path.join(base_dir, 'var_spec_add.csv'))

df_rois = df_rois.rename(columns={'variable': 'channel','spend_sum': 'spend'})

# print('df_rois:', df_rois.shape)
# print('df_decomp_vol:', df_decomp_vol.shape)
# print('df_var_spec:', df_var_spec.shape)
# display(df_rois.head())
# display(df_decomp_vol.head())
# display(df_var_spec.head())

In [42]:
df_media_results

channel distribution impressions % impressions        spend  \
0          m_wow_tv        prior   2,699,491         15.5%   $2,699,491   
1          m_wow_tv    posterior   2,699,491         15.5%   $2,699,491   
2         m_wow_olv        prior     947,317          5.4%     $947,317   
3         m_wow_olv    posterior     947,317          5.4%     $947,317   
4      m_wow_social        prior     121,919          0.7%     $121,919   
5      m_wow_social    posterior     121,919          0.7%     $121,919   
6       m_amaze_tot        prior   7,929,905         45.6%   $7,929,905   
7       m_amaze_tot    posterior   7,929,905         45.6%   $7,929,905   
8        m_celeb_tv        prior   2,828,021         16.2%   $2,828,021   
9        m_celeb_tv    posterior   2,828,021         16.2%   $2,828,021   
10  m_celeb_outdoor        prior   1,290,619          7.4%   $1,290,619   
11  m_celeb_outdoor    posterior   1,290,619          7.4%   $1,290,619   
12  m_celeb_display        prior   1,586,718          9.1%   $1,586,718   
13  m_celeb_display    posterior   1,586,718          9.1%   $1,586,718   
14     All Channels        prior  17,403,992        100.0%  $17,403,992   
15     All Channels    posterior  17,403,992        100.0%  $17,403,992   

   % spend     cpm                     incremental outcome  \
0    15.5%  $1,000      $4,861,564 ($790,373, $14,571,438)   
1    15.5%  $1,000       $1,857,861 ($747,814, $3,072,498)   
2     5.4%  $1,000       $1,634,362 ($260,968, $4,486,518)   
3     5.4%  $1,000       $1,262,348 ($296,897, $2,761,044)   
4     0.7%  $1,000            $222,156 ($28,004, $617,307)   
5     0.7%  $1,000            $164,626 ($30,298, $442,521)   
6    45.6%  $1,000   $14,108,085 ($2,325,067, $38,368,352)   
7    45.6%  $1,000     $7,368,084 ($5,823,471, $8,949,739)   
8    16.2%  $1,000      $5,132,303 ($786,984, $15,284,361)   
9    16.2%  $1,000     $4,449,494 ($2,278,418, $6,866,625)   
10    7.4%  $1,000       $2,164,558 ($339,727, $6,209,604)   
11    7.4%  $1,000         $814,976 ($253,850, $1,578,369)   
12    9.1%  $1,000       $2,863,339 ($450,047, $8,097,693)   
13    9.1%  $1,000         $952,830 ($244,328, $2,169,385)   
14  100.0%  $1,000  $30,986,376 ($13,564,848, $59,760,340)   
15  100.0%  $1,000  $16,870,208 ($12,966,289, $20,967,838)   

        % contribution             roi      effectiveness            mroi  \
0    1.0% (0.2%, 3.1%)  1.8 (0.3, 5.4)  1.80 (0.29, 5.40)  1.0 (0.1, 2.7)   
1    0.5% (0.2%, 0.8%)  0.7 (0.3, 1.1)  0.69 (0.28, 1.14)  0.4 (0.1, 0.7)   
2    0.4% (0.1%, 1.0%)  1.7 (0.3, 4.7)  1.73 (0.28, 4.74)  0.8 (0.1, 2.3)   
3    0.3% (0.1%, 0.7%)  1.3 (0.3, 2.9)  1.33 (0.31, 2.91)  0.6 (0.1, 1.3)   
4    0.0% (0.0%, 0.1%)  1.8 (0.2, 5.1)  1.82 (0.23, 5.06)  0.5 (0.1, 1.5)   
5    0.0% (0.0%, 0.1%)  1.4 (0.2, 3.6)  1.35 (0.25, 3.63)  0.4 (0.1, 1.0)   
6    3.0% (0.5%, 8.3%)  1.8 (0.3, 4.8)  1.78 (0.29, 4.84)  0.9 (0.1, 2.5)   
7    1.8% (1.4%, 2.2%)  0.9 (0.7, 1.1)  0.93 (0.73, 1.13)  0.5 (0.3, 0.7)   
8    1.1% (0.2%, 3.3%)  1.8 (0.3, 5.4)  1.81 (0.28, 5.40)  0.8 (0.1, 2.6)   
9    1.1% (0.6%, 1.7%)  1.6 (0.8, 2.4)  1.57 (0.81, 2.43)  0.9 (0.4, 1.5)   
10   0.5% (0.1%, 1.3%)  1.7 (0.3, 4.8)  1.68 (0.26, 4.81)  0.7 (0.1, 2.1)   
11   0.2% (0.1%, 0.4%)  0.6 (0.2, 1.2)  0.63 (0.20, 1.22)  0.3 (0.1, 0.6)   
12   0.6% (0.1%, 1.7%)  1.8 (0.3, 5.1)  1.80 (0.28, 5.10)  0.9 (0.1, 2.7)   
13   0.2% (0.1%, 0.5%)  0.6 (0.2, 1.4)  0.60 (0.15, 1.37)  0.3 (0.1, 0.7)   
14  6.7% (2.9%, 12.9%)  1.8 (0.8, 3.4)     nan (nan, nan)  nan (nan, nan)   
15   4.2% (3.2%, 5.2%)  1.0 (0.7, 1.2)     nan (nan, nan)  nan (nan, nan)   

                  cpik  
0    $1.9 ($0.4, $7.8)  
1    $3.4 ($2.0, $8.2)  
2    $1.8 ($0.5, $8.1)  
3    $1.9 ($0.8, $7.2)  
4    $1.7 ($0.4, $9.7)  
5    $2.2 ($0.6, $9.0)  
6    $2.0 ($0.5, $8.2)  
7    $2.6 ($2.1, $3.3)  
8    $2.0 ($0.5, $8.8)  
9    $1.6 ($1.0, $3.0)  
10   $2.1 ($0.5, $9.2)  
11  $4.2 ($2.0, $12.3)  
12   $2.1 ($0.5, $8.7)  
13  $4.8 ($1.8, $16.0

In [43]:
posterior_mask = df_media_results['distribution'].str.lower().str.contains('posterior')
df_post = df_media_results[posterior_mask].copy()
df_post = df_post[['channel','spend','incremental outcome','roi']]


In [44]:
# Clean 'incremental outcome' and 'roi' columns: extract value before bracket, remove $/commas, convert to number
import re

def clean_value(val):
    if pd.isnull(val):
        return None
    # Take value before first bracket
    s = str(val).split('(')[0].strip()
    # Remove $ and commas
    s = re.sub(r'[$,]', '', s)
    try:
        return float(s)
    except Exception:
        return None

cols_to_clean = ['incremental outcome', 'roi']
if all(col in df_post.columns for col in cols_to_clean):
    df_post_clean = df_post.copy()
    for col in cols_to_clean:
        df_post_clean[col] = df_post_clean[col].apply(clean_value)
    display(df_post_clean[['channel', 'spend', 'incremental outcome', 'roi']])
else:
    print("Some required columns missing in df_post. Available columns:", df_post.columns.tolist())

channel        spend  incremental outcome  roi
1          m_wow_tv   $2,699,491            1857861.0  0.7
3         m_wow_olv     $947,317            1262348.0  1.3
5      m_wow_social     $121,919             164626.0  1.4
7       m_amaze_tot   $7,929,905            7368084.0  0.9
9        m_celeb_tv   $2,828,021            4449494.0  1.6
11  m_celeb_outdoor   $1,290,619             814976.0  0.6
13  m_celeb_display   $1,586,718             952830.0  0.6
15     All Channels  $17,403,992           16870208.0  1.0

In [45]:
df_post = df_post_clean.rename(columns={'spend': 'spend (mer)','incremental outcome':'value (mer)', 'roi':'roi (mer)'})
# df_post[df_post['channel'] == 'All Channels'].loc['channel']="Total"
idx = df_post.index[df_post['channel'] == 'All Channels']
df_post.loc[idx, 'channel'] = 'Total'



In [48]:
merged = df_rois.merge(df_post, on='channel', how='left', suffixes=('', '_rois'))
clean_numeric_dataframe(merged, exclude=['channel', 'variable'], in_place=True)

merged['roi']=merged['roi']/4
merged['roi (est)']=merged['roi (est)']/4

# Percent change calculations
merged['%_change_spend'] = 100 * (merged['spend (mer)'] - merged['spend']) / merged['spend']
merged['%_change_value'] = 100 * (merged['value (mer)'] - merged['value']) / merged['value']
merged['%_change_roi'] = 100 * (merged['roi (mer)'] - merged['roi']) / merged['roi']

# Optional: format as string with 2 decimals
merged['spend'] = merged['spend'].map('{:,.2f}'.format)
merged['value'] = merged['value'].map('{:,.2f}'.format)
merged['value (mer)'] = merged['value (mer)'].map('{:,.2f}'.format)
merged['roi'] = merged['roi'].map('{:,.1f}'.format)
merged['roi (est)'] = merged['roi (est)'].map('{:,.1f}'.format)
merged['roi (mer)'] = merged['roi (mer)'].map('{:,.2f}'.format)

merged['%_change_spend'] = merged['%_change_spend'].map('{:+.1f}%'.format)
merged['%_change_value'] = merged['%_change_value'].map('{:+.1f}%'.format)
merged['%_change_roi'] = merged['%_change_roi'].map('{:+.1f}%'.format)

merged

channel          value          spend  roi roi (est)  \
0         m_wow_tv   8,153,785.00   2,699,491.00  0.8       1.0   
1        m_wow_olv   2,121,312.00     947,317.00  0.6       1.0   
2     m_wow_social     213,268.00     121,919.00  0.4      -3.2   
3      m_amaze_tot  25,532,763.00   7,929,905.00  0.8       0.8   
4       m_celeb_tv   9,193,975.00   2,828,021.00  0.8       0.9   
5  m_celeb_outdoor   4,194,756.00   1,290,619.00  0.8       0.1   
6  m_celeb_display   2,606,237.00   1,586,718.00  0.4       1.5   
7            Total  52,016,095.00  17,403,991.00  0.7       0.8   

   % change (est/actual)  spend (mer)    value (mer) roi (mer) %_change_spend  \
0                  28.48    2699491.0   1,857,861.00      0.70          +0.0%   
1                  84.82     947317.0   1,262,348.00      1.30          +0.0%   
2                -822.86     121919.0     164,626.00      1.40          +0.0%   
3                   0.62    7929905.0   7,368,084.00      0.90          +0.0%   
4                   6.15    2828021.0   4,449,494.00      1.60          +0.0%   
5                 -82.77    1290619.0     814,976.00      0.60          +0.0%   
6                 264.63    1586718.0     952,830.00      0.60          +0.0%   
7                  12.37   17403992.0  16,870,208.00      1.00          +0.0%   

  %_change_value %_change_roi  
0         -77.2%        -7.3%  
1         -40.5%      +132.1%  
2         -22.8%      +220.0%  
3         -71.1%       +11.8%  
4         -51.6%       +96.9%  
5         -80.6%       -26.2%  
6         -63.4%       +46.3%  
7         -67.6%       +33.8%

In [49]:
merged_rois = merged[['channel', 'spend', 'roi',  'roi (est)', 'roi (mer)']]

merged_rois

channel          spend  roi roi (est) roi (mer)
0         m_wow_tv   2,699,491.00  0.8       1.0      0.70
1        m_wow_olv     947,317.00  0.6       1.0      1.30
2     m_wow_social     121,919.00  0.4      -3.2      1.40
3      m_amaze_tot   7,929,905.00  0.8       0.8      0.90
4       m_celeb_tv   2,828,021.00  0.8       0.9      1.60
5  m_celeb_outdoor   1,290,619.00  0.8       0.1      0.60
6  m_celeb_display   1,586,718.00  0.4       1.5      0.60
7            Total  17,403,991.00  0.7       0.8      1.00